# Visualizing NYC Taxi Trips with Datashader, Altair, and Panel

In this notebook, we create an example dashboard visualizing NYC taxi trip data. The dashboard includes:

- a heatmap of the taxi trips using Holoviews and Datashader
- a histogram of the passenger counts using Altair
- lots of Panel-based widgets for controlling the map aesthetics
- a Holoviews selection stream that links the map x/y ranges to the histogram plot

As the user zooms in/out of the map, the Altair chart updates to show only data currently within the map viewport.

This dashboard is adapted from the [example dashboard](http://datashader.org/dashboard.html) on the Datashader documentation.


#### References

For more information, see the documentation:

- [Panel User Guide](https://panel.pyviz.org/user_guide/index.html)
- [Panel Reference Gallery](https://panel.pyviz.org/reference/index.html)
    - Includes examples of different types of Panels, e.g., HTML, Markdown, Vega, etc
- [Examples of Panel dashboards from the PyViz team](https://github.com/pyviz-demos)
- [Datashader dashboard documentation](http://datashader.org/dashboard.html)
    - Including a detailed walk-through of many of the steps used in this dashboard

In [21]:
import numpy as np
import pandas as pd
import altair as alt
import dask.dataframe as dd
import holoviews as hv
import geoviews.tile_sources as gts
import param as pm
import panel as pn
import colorcet
import datashader as ds
from holoviews.operation.datashader import rasterize, shade, spread

In [9]:
# Enable Altair and Holoviews rendering in the notebook
alt.renderers.enable('notebook')
hv.extension('bokeh')

In [60]:
# Add the Vega extension for Panel
pn.extension('vega')

## Load the full data set

We'll use Dask to load a data set of over 1 million taxi trips in NYC. The data is available for download
at:

> https://s3.amazonaws.com/datashader-data/nyc_taxi_wide.parq 


**Important** 

If you are working locally, you must download the data and place it in the `data/` folder, but if you are working on Binder, the data should already be available.

In [37]:
# select only a subset of columns
usecols = ['dropoff_x','dropoff_y','pickup_x','pickup_y','dropoff_hour','pickup_hour','passenger_count']

# use dask to load the data
df = dd.read_parquet('data/nyc_taxi_wide.parq')[usecols].persist()

**Note**

We'll load the *full* data above, and when the user changes input parameters, we'll filter the full data set in our app according to those parameters.

## Build the app

We'll define our app as a custom Python class that defines the various components of our dashboard, which include:

- The parameters we want the user to be able to change.
- Functions to generate the various charts/maps in our dashboard, based on those input parameters.
- The dependencies between our chart functions and parameters.

In [74]:
# Create a dictionary of color maps from colorcet
cmap_names = ["bgy", "fire", "bgyw", "bmy", "gray", "kbc"]
cmaps = {n: colorcet.palette[n] for n in cmap_names}

# Create a dictionary of different basemap tiles from Geoviews
maps = ["CartoDark", "CartoLight"]
bases = {name: gts.tile_sources[name].relabel(name) for name in maps}

# Define the options for the basemap tiles that we'll use
gopts = hv.opts.WMTS(xaxis=None, yaxis=None, bgcolor="black", show_grid=False)

In [123]:
class NYCTaxiApp(pm.Parameterized):
    """
    A Panel-based dashboard app visualizing data for over a million 
    NYC taxi trips.
    
    The app has three main components:
        1. A datashaded heatmap of taxi trips
        2. A set of widgets controlling the data plotted on the map
        3. A histogram of the number of passengers  per trip
        
    The histogram is linked to the Holoviews map and only plots the 
    histogram of data currently displayed on the map. 
    """

    # the dropoff hour
    hour = pm.Range(default=(0, 24), bounds=(0, 24))

    # pickups or dropoffs
    location = pm.ObjectSelector(default="dropoff", objects=["dropoff", "pickup"])

    # colormap and pixel spreading
    cmap = pm.Selector(cmaps)
    spreading = pm.Integer(0, bounds=(0, 5))

    # basemap tiles
    basemap = pm.Selector(bases)

    # map options
    data_opacity = pm.Magnitude(1.00)
    map_opacity = pm.Magnitude(0.75)
    show_labels = pm.Boolean(False)

    # selection that gives the current x_range/y_range of the map
    box = hv.streams.RangeXY(x_range=None, y_range=None)

    @pm.depends("location", "hour")
    def points(self, x_range=None, y_range=None):
        """
        Get a Holoviews.Points object holding the taxi data. 
        
        Before returning, filter the points by dropoff hour 
        and x/y range.
        """
        # create the Points object holding all data
        xcol = self.location + "_x"
        ycol = self.location + "_y"
        points = hv.Points(df, kdims=[xcol, ycol], vdims=["dropoff_hour"])

        # trim by dropoff hour
        if self.hour != (0, 24):
            points = points.select(dropoff_hour=self.hour)

        # trim by x range of plot
        if x_range is not None:
            points = points.select(**{xcol: x_range})

        # trim by y range of plot
        if y_range is not None:
            points = points.select(**{ycol: y_range})

        return points

    @pm.depends("map_opacity", "basemap")
    def tiles(self):
        """
        Get the basemap tiles from the specified tile provider and
        with the specified map opacity level.
        """
        return self.basemap.opts(gopts).opts(alpha=self.map_opacity)

    @pm.depends("show_labels")
    def labels(self):
        """
        Return the labels. If hidden, set the opacity to 0.
        """
        alpha = 1 if self.show_labels else 0
        return gts.StamenLabels.options(level="annotation", alpha=alpha)

    def heatmap(self, **kwargs):
        """
        Return a datashaded heatmap of the taxi trips.
        """

        # create a dynamic map using the points() function
        # and link the box selection stream to the map
        points = hv.DynamicMap(self.points, streams=[self.box])

        # aggregate the points by counting them up on a mesh
        rasterized = rasterize(points, aggregator=ds.count(), width=800, height=400)

        # do the datashading operation with the specified color map
        shaded = shade(rasterized, cmap=self.param.cmap, normalization="eq_hist")

        # should we spread out points over multiple pixels
        spreaded = spread(shaded, px=self.param.spreading, how="add")

        # apply the opacity option
        dataplot = spreaded.apply.opts(alpha=self.param.data_opacity, show_legend=False)

        # return the combined chart
        final = hv.DynamicMap(self.tiles) * dataplot * hv.DynamicMap(self.labels)
        return final.options(
            default_tools=["save", "pan", "box_zoom", "reset"],
            active_tools=["box_zoom"],
            width=600,
            height=400,
        )

    @pm.depends("hour", "box.x_range", "box.y_range")
    def passenger_hist(self):
        """
        Return an Altair histogram showing the number of passengers 
        per trip.
        
        This chart depends on the box selection's x/y range and will be 
        re-drawn when the bounds of the map are updated by the user.
        """

        # get the currently displayed points
        points = self.points(x_range=self.box.x_range, y_range=self.box.y_range)

        # use numpy to get a histogram of the passenger count
        counts, bin_edges = np.histogram(points.data.passenger_count, bins="auto")
        bin_centers = 0.5 * (bin_edges[1:] + bin_edges[:-1])
        hist = pd.DataFrame(
            {"Number of Trips": counts, "Number of Passengers": bin_centers}
        )

        # make the Altair chart
        chart = (
            alt.Chart(hist)
            .mark_bar()
            .encode(x="Number of Passengers", y="Number of Trips")
            .properties(width=500, height=300)
        )

        return pn.Pane(chart, width=800)

In [134]:
# initialize our app
app = NYCTaxiApp(name="")

## Layout our Panel object

We will use a combination of the `Column()` and `Row()` objects to create out layout. Also, we can use the `Spacer()` object to explicitly add more blank space of fixed width/height.

In [135]:
title = pn.pane.HTML(
    "<h2>Visualizing NYC Taxi Trips with Datashader, Altair, and Panel</h2>",
    style={"width": "800px", "text-align": "center"},
)
hist_title = pn.pane.HTML(
    "<h3>How Many Passengers Does a Typical Taxi Trip Have?</h3>",
    style={"width": "800px", "text-align": "center"},
)

In [136]:
panel = pn.Column(
    pn.Row(title),
    pn.Row(pn.Param(app.param, expand_button=False, width=200), app.heatmap()),
    pn.Row(hist_title),
    pn.Row(pn.Spacer(width=75), app.passenger_hist),
    align='center',
    width=1200
)

### Call servable() and render our Panel object

This will do two things: 

1. Render the dashboard in the notebook
2. Enables the notebook to be served from `localhost`. We can execute `panel serve --show app.ipynb` from the command line and see the app live at `http://localhost:5006/app`

In [137]:
panel.servable()

Column(align='center', width=1200)
    [0] Row
        [0] HTML(str, style={'width': '800px', ...})
    [1] Row
        [0] Param(NYCTaxiApp, expand_button=False, width=200)
        [1] HoloViews(DynamicMap)
    [2] Row
        [0] HTML(str, style={'width': '800px', ...})
    [3] Row
        [0] Spacer(width=75)
        [1] ParamMethod(method)